In [ ]:
import csv
import os

import datasets

_DESCRIPTION = """
The datasets were collected and published to present the educational level of NC population in different areas. The educational attainment for the black population data can raise concern for the educational equity issue in North Carolina. The combined dataset aims to offer a holistic perspective on educational levels and equity, with a specific focus on the educational attainment of the Black population aged 25 and over.
"""

_HOMEPAGE = "https://huggingface.co/datasets/YXu120/NC_Education"

_LICENSE = "cc-by-sa-4.0"

_URL = "https://drive.google.com/file/d/1Au9xwsnDkRx4TMWwndWKbzLR5u9WXUQZ/view?usp=sharing"

class NCEducationDataset(datasets.GeneratorBasedBuilder):
    _URL = _URL

    VERSION = datasets.Version("1.0.0")

    def _info(self):
        features = datasets.Features(
            {
                "area_name": datasets.Value("string"),
                "area_type": datasets.Value("string"),
                "years": datasets.Sequence(
                    {
                        "year": datasets.Value("int"),
                        "variables": datasets.Sequence(
                            {
                                "variable": datasets.Value("string"),
                                "value": datasets.Value("int"),
                                "value_black": datasets.Value("int")
                            }
                        )
                    }
                )
            }
        )

        return datasets.DatasetInfo(
            description=_DESCRIPTION,
            features=features,
            homepage=_HOMEPAGE,
            license=_LICENSE,
        )

    def _split_generators(self, dl_manager):
        data_file = dl_manager.download(self._URL)
        return [
            datasets.SplitGenerator(
                name="train",
                gen_kwargs={
                    "filepath": data_file,
                },
            )
        ]

    def _generate_examples(self, filepath):
        data = {}
        with open(filepath, "r", encoding="utf-8") as file:
            csv_reader = csv.DictReader(file)
            for row in csv_reader:
                area_name = row["area_name"]
                area_type = row["area_type"]
                year = int(row["year"])
                variable = row["variable"]
                value = int(row["value"]) if row["value"] else None
                value_black = int(row["value_black"]) if row["value_black"] else None

                if area_name not in data:
                    data[area_name] = {
                        "area_type": area_type,
                        "years": {}
                    }

                if year not in data[area_name]["years"]:
                    data[area_name]["years"][year] = []

                data[area_name]["years"][year].append({
                    "variable": variable,
                    "value": value,
                    "value_black": value_black
                })

        for idx, (area_name, area_data) in enumerate(data.items()):
            years_data = []
            for year, variables in area_data["years"].items():
                year_data = {
                    "year": year,
                    "variables": variables
                }
                years_data.append(year_data)

            yield idx, {
                "area_name": area_name,
                "area_type": area_data["area_type"],
                "years": years_data
            }